In [2]:
# !pip install learntools==0.3.4

In [3]:
# !pip install statsmodels

In [4]:
# # Setup feedback system
# from learntools.core import binder
# binder.bind(globals())
# from learntools.time_series.ex3 import *

# Setup notebook
from pathlib import Path
# from learntools.time_series.style import *  # plot style settings
# from learntools.time_series.utils import plot_periodogram, seasonal_plot

import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import seaborn as sns
from sklearn.linear_model import LinearRegression
from statsmodels.tsa.deterministic import CalendarFourier, DeterministicProcess


# comp_dir = Path('/Users/harikrishnadev/Library/Mobile Documents/com~apple~CloudDocs/School Work/Sem 2/BUAN 6312/Group project/store-sales-time-series-forecasting')

holidays_events = pd.read_csv(
     "holidays_events.csv",
    dtype={
        'type': 'category',
        'locale': 'category',
        'locale_name': 'category',
        'description': 'category',
        'transferred': 'bool',
    },
    parse_dates=['date'],
    infer_datetime_format=True,
)
holidays_events = holidays_events.set_index('date').to_period('D')

store_sales = pd.read_csv(
    'train.csv',
    dtype={
        'store_nbr': 'category',
        'family': 'category',
        'sales': 'float32',
    },
    parse_dates=['date'],
    infer_datetime_format=True,
)
store_sales['date'] = store_sales.date.dt.to_period('D')


/var/folders/3d/fk1zpy415g31bg07yrkc5qbm0000gn/T/ipykernel_87427/1091318273.py:21: FutureWarning: The argument 'infer_datetime_format' is deprecated and will be removed in a future version. A strict version of it is now the default, see https://pandas.pydata.org/pdeps/0004-consistent-to-datetime-parsing.html. You can safely remove this argument.
  holidays_events = pd.read_csv(
/var/folders/3d/fk1zpy415g31bg07yrkc5qbm0000gn/T/ipykernel_87427/1091318273.py:35: FutureWarning: The argument 'infer_datetime_format' is deprecated and will be removed in a future version. A strict version of it is now the default, see https://pandas.pydata.org/pdeps/0004-consistent-to-datetime-parsing.html. You can safely remove this argument.
  store_sales = pd.read_csv(


In [5]:
store_sales.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3000888 entries, 0 to 3000887
Data columns (total 6 columns):
 #   Column       Dtype    
---  ------       -----    
 0   id           int64    
 1   date         period[D]
 2   store_nbr    category 
 3   family       category 
 4   sales        float32  
 5   onpromotion  int64    
dtypes: category(2), float32(1), int64(2), period[D](1)
memory usage: 85.9 MB


In [6]:
store_sales = store_sales.groupby(['date','store_nbr'])['sales'].sum()

In [7]:
store_sales = store_sales.reset_index()

In [8]:
store_sales.head()

date store_nbr  sales
0  2013-01-01         1    0.0
1  2013-01-01        10    0.0
2  2013-01-01        11    0.0
3  2013-01-01        12    0.0
4  2013-01-01        13    0.0

In [9]:
oil = pd.read_csv(
    'oil.csv',
    parse_dates=['date'],
    infer_datetime_format=True,
)
oil['date'] = oil.date.dt.to_period('D')

/var/folders/3d/fk1zpy415g31bg07yrkc5qbm0000gn/T/ipykernel_87427/3932573575.py:1: FutureWarning: The argument 'infer_datetime_format' is deprecated and will be removed in a future version. A strict version of it is now the default, see https://pandas.pydata.org/pdeps/0004-consistent-to-datetime-parsing.html. You can safely remove this argument.
  oil = pd.read_csv(


In [10]:
oil["date"].dt.day.unique()

array([ 1,  2,  3,  4,  7,  8,  9, 10, 11, 14, 15, 16, 17, 18, 21, 22, 23,
       24, 25, 28, 29, 30, 31,  5,  6, 12, 13, 19, 20, 26, 27])

In [11]:
# stores = pd.read_csv(
#     'stores.csv'
# )
# stores.head()

In [12]:
import datetime
store_sales["month"]=store_sales["date"].dt.month
store_sales["weekday"]=store_sales["date"].dt.weekday

In [13]:
store_sales.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 90936 entries, 0 to 90935
Data columns (total 5 columns):
 #   Column     Non-Null Count  Dtype    
---  ------     --------------  -----    
 0   date       90936 non-null  period[D]
 1   store_nbr  90936 non-null  category 
 2   sales      90936 non-null  float32  
 3   month      90936 non-null  int64    
 4   weekday    90936 non-null  int64    
dtypes: category(1), float32(1), int64(2), period[D](1)
memory usage: 2.5 MB


In [14]:
store_sales["date"].unique()

<PeriodArray>
['2013-01-01', '2013-01-02', '2013-01-03', '2013-01-04', '2013-01-05',
 '2013-01-06', '2013-01-07', '2013-01-08', '2013-01-09', '2013-01-10',
 ...
 '2017-08-06', '2017-08-07', '2017-08-08', '2017-08-09', '2017-08-10',
 '2017-08-11', '2017-08-12', '2017-08-13', '2017-08-14', '2017-08-15']
Length: 1684, dtype: period[D]

In [15]:
# median_oil = oil["dcoilwtico"].median()
# median_oil

In [16]:
oil["dcoilwtico"] = np.where(oil["dcoilwtico"] == 0, np.nan, oil["dcoilwtico"])
oil["dcoilwtico_interpolated"] =oil.dcoilwtico.interpolate()


In [17]:
# store_sales["dcoilwtico"] = store_sales["dcoilwtico"].fillna()

In [18]:
store_sales.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 90936 entries, 0 to 90935
Data columns (total 5 columns):
 #   Column     Non-Null Count  Dtype    
---  ------     --------------  -----    
 0   date       90936 non-null  period[D]
 1   store_nbr  90936 non-null  category 
 2   sales      90936 non-null  float32  
 3   month      90936 non-null  int64    
 4   weekday    90936 non-null  int64    
dtypes: category(1), float32(1), int64(2), period[D](1)
memory usage: 2.5 MB


In [19]:
store_sales = store_sales.merge(holidays_events,on="date",how="left")

In [20]:
store_sales = store_sales.merge(oil,on="date",how="left")

In [21]:
# !pip install plotly

In [22]:
import plotly.express as px
px.scatter(store_sales, x = "dcoilwtico_interpolated", y = "sales", trendline = "ols", trendline_color_override = "red",color_discrete_sequence=px.colors.qualitative.Set2)

In [23]:
store_nbr = pd.read_csv(
    'stores.csv'
)
store_sales = store_sales.merge(store_nbr,on="store_nbr",how="left")

In [24]:
dummies = pd.get_dummies(store_sales['month'], prefix='month', prefix_sep='')
# dummies.columns = ['jan', 'feb', 'mar', 'apr', 'may', 'jun', 'jul', 'aug', 'sep', 'oct', 'nov', 'dec']
store_sales = pd.concat([store_sales, dummies], axis=1)

In [25]:
# dummies = pd.get_dummies(store_sales['day'], prefix='day', prefix_sep='_')
# store_sales = pd.concat([store_sales, dummies], axis=1)

In [26]:
# dummies = pd.get_dummies(store_sales['week'], prefix='week', prefix_sep='_')
# store_sales = pd.concat([store_sales, dummies], axis=1)

In [27]:
dummies = pd.get_dummies(store_sales['weekday'], prefix='week', prefix_sep='_')
store_sales = pd.concat([store_sales, dummies], axis=1)

In [28]:
# dummies = pd.get_dummies(store_sales['year'], prefix='year', prefix_sep='_')
# store_sales = pd.concat([store_sales, dummies], axis=1)

In [29]:
store_sales.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 92556 entries, 0 to 92555
Data columns (total 35 columns):
 #   Column                   Non-Null Count  Dtype    
---  ------                   --------------  -----    
 0   date                     92556 non-null  period[D]
 1   store_nbr                92556 non-null  object   
 2   sales                    92556 non-null  float32  
 3   month                    92556 non-null  int64    
 4   weekday                  92556 non-null  int64    
 5   type_x                   15228 non-null  category 
 6   locale                   15228 non-null  category 
 7   locale_name              15228 non-null  category 
 8   description              15228 non-null  category 
 9   transferred              15228 non-null  object   
 10  dcoilwtico               63612 non-null  float64  
 11  dcoilwtico_interpolated  65880 non-null  float64  
 12  city                     0 non-null      object   
 13  state                    0 non-null      objec

In [30]:
# store_sales["month"].unique()

array([ 1,  2,  3,  4,  5,  6,  7,  8,  9, 10, 11, 12])

In [ ]:
# store_sales.drop(["id"],axis=1,inplace=True)

In [33]:
# store_sales['transferred'] = store_sales['transferred'].fillna(0).astype(int)

In [34]:
from statsmodels.tsa.stattools import adfuller

#perform augmented Dickey-Fuller test
adfuller(store_sales["sales"])

(-14.37818085538618,
 9.248325968568031e-27,
 67,
 92488,
 {'1%': -3.430420706270036,
  '5%': -2.861571251035633,
  '10%': -2.5667866338375953},
 1803231.2465499912)

In [35]:
from statsmodels.tsa.stattools import kpss
kpss(store_sales["sales"],nlags='auto',regression='c',store=False)

/var/folders/3d/fk1zpy415g31bg07yrkc5qbm0000gn/T/ipykernel_87427/565107455.py:2: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is smaller than the p-value returned.




(41.020463739560185,
 0.01,
 143,
 {'10%': 0.347, '5%': 0.463, '2.5%': 0.574, '1%': 0.739})

In [44]:
diff = store_sales["sales"].diff()

In [36]:
# adfuller(store_sales["dcoilwtico_interpolated"])

In [50]:
diff.replace([np.inf, -np.inf], 0, inplace=True)
diff = diff.dropna()

In [51]:
from statsmodels.tsa.stattools import adfuller

#perform augmented Dickey-Fuller test
adfuller(diff)

(-55.357628699923914,
 0.0,
 67,
 92487,
 {'1%': -3.4304207070345565,
  '5%': -2.8615712513735345,
  '10%': -2.566786634017449},
 1803179.2097510933)

In [52]:
from statsmodels.tsa.stattools import kpss
kpss(diff,nlags='auto',regression='c',store=False)

/var/folders/3d/fk1zpy415g31bg07yrkc5qbm0000gn/T/ipykernel_87427/3118771864.py:2: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is greater than the p-value returned.




(0.002439759936336917,
 0.1,
 391,
 {'10%': 0.347, '5%': 0.463, '2.5%': 0.574, '1%': 0.739})